## import libraries

In [3]:
import sys
import os

In [4]:
print(os.getcwd())

/home/jjoy/projects/BTE-RAG/notebooks


In [5]:
this_dir = os.getcwd()
project_root = os.path.abspath(os.path.join(this_dir, os.pardir))
if project_root not in sys.path:
    sys.path.insert(0, project_root)
os.chdir(project_root)

In [6]:
print(os.getcwd())

/home/jjoy/projects/BTE-RAG


In [8]:
import kg_rag.util as funct
from kg_rag.util import * 


In [3655]:
!pip list --format=freeze | grep openai

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
openai==1.61.0


In [ ]:
!pip list | grep openai #1.61.0

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
openai                    1.61.0


In [9]:
import tiktoken
encoding = tiktoken.encoding_for_model('gpt-4o')
print(encoding)

<Encoding 'o200k_base'>


In [10]:
import tiktoken
encoding = tiktoken.encoding_for_model('gpt-4o-mini')
print(encoding)

<Encoding 'o200k_base'>


In [4464]:
def num_tokens_from_string(string: str, encoding_name: str) -> int:
    """Returns the number of tokens in a text string."""
    encoding = tiktoken.get_encoding(encoding_name)
    num_tokens = len(encoding.encode(string))
    return num_tokens

In [4465]:
def extract_answer(llm_answer_prompt_test):
    llm_answer_prompt_test = llm_answer_prompt_test.replace('```json\n', '').replace('```', '')
    llm_answer = json.loads(llm_answer_prompt_test)
    return llm_answer['answer']

In [3]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', None)

In [13]:
sentence_embedding_model='pritamdeka/S-PubMedBert-MS-MARCO'
embedding_function = load_sentence_transformer(sentence_embedding_model)

In [11]:
config_data["SENTENCE_EMBEDDING_MODEL_FOR_CONTEXT_RETRIEVAL"]

'pritamdeka/S-PubMedBert-MS-MARCO'

# DrugmechDB Mechanistic questions

In [16]:
drugmechdb_filtered_df = pd.read_csv("DMDB_benchmark/Benchmarks/DMDB_mechanistic_genes_filtered.csv")
drugmechdb_filtered_df.shape

(798, 11)

In [17]:
drugmechdb_filtered_df.head(1)

id        drug   Drug_MeshID       disease  \
0  ['DB01219_MESH_C535694_1']  DB:DB01219  MESH:D003620  MESH:C535694   

              protein   drug_name            disease_name  \
0  ['UniProt:P21817']  Dantrolene  Malignant hyperthermia   

               protein_name protein_gene_symbol  \
0  ['Ryanodine receptor 1']            ['RYR1']   

                                            question  count  
0  Which gene plays the most significant mechanis...      1

In [28]:
drugmechdb_filtered_df["Drug_MeshID"] = drugmechdb_filtered_df["Drug_MeshID"].str.replace(r"^DB:", "DRUGBANK:", regex=True)

In [29]:
drugmechdb_filtered_df["drug"] = drugmechdb_filtered_df["drug"].str.replace(r"^DB:", "DRUGBANK:", regex=True)

In [30]:
drugmechdb_filtered_df.head(1)

id              drug   Drug_MeshID       disease  \
0  ['DB01219_MESH_C535694_1']  DRUGBANK:DB01219  MESH:D003620  MESH:C535694   

              protein   drug_name            disease_name  \
0  ['UniProt:P21817']  Dantrolene  Malignant hyperthermia   

               protein_name protein_gene_symbol  \
0  ['Ryanodine receptor 1']            ['RYR1']   

                                            question  count  
0  Which gene plays the most significant mechanis...      1

In [31]:
df_drug = drugmechdb_filtered_df[["Drug_MeshID", "drug_name"]]
print(df_drug.shape)
df_drug[df_drug.duplicated(keep=False)].value_counts()

(798, 2)


Drug_MeshID       drug_name                  
DRUGBANK:DB00394  Beclomethasone dipropionate    5
MESH:D064747      lansoprazole                   5
MESH:D000865      Antazoline                     5
MESH:D000068579   celecoxib                      5
MESH:D014859      warfarin                       5
                                                ..
MESH:C005386      Tridihexethyl                  2
MESH:D053590      Anakinra                       2
MESH:D061268      insulin lispro                 2
MESH:D000068677   Sildenafil                     2
MESH:D000069439   Dasatinib                      2
Name: count, Length: 168, dtype: int64

In [32]:
drugmechdb_drug = drugmechdb_filtered_df[["Drug_MeshID", "drug_name"]].drop_duplicates()
drugmechdb_disease = drugmechdb_filtered_df[["disease", "disease_name"]].drop_duplicates()

In [33]:
print(drugmechdb_drug.shape)
print(drugmechdb_disease.shape)

(508, 2)
(295, 2)


# BTE Parquet file

### Mechanistic gene

In [2671]:
def get_node_context(doid, is_disease=True):
   
    try:
        # Set category based on whether the input is a disease or drug
        category = "biolink:Disease" if is_disease else "biolink:ChemicalEntity"
        
        # Base URI for BTE API
        base_uri = "https://bte.transltr.io/v1/query"
        
        # Construct the query
        query = {
            "message": {
                "query_graph": {
                    "nodes": {
                        "n0": {
                            "categories": [category],
                            "ids": [doid]
                        },
                        "n1": {
                            "categories": ["biolink:Gene", "biolink:Protein"]
                        }
                    },
                    "edges": {
                        "e01": {
                            "subject": "n0",
                            "object": "n1"
                        }
                    }
                }
            }
        }
        
        # Call the BTE API
        print("query:", query)
        result = get_bte_api_resp(base_uri, query)
        
        # Handle API response
        if result.get('status') == 500:
            print(f"Error from BTE API for DOID {doid}: {result['description']}")
            return None
        
        # Return node context
        return result
    
    except Exception as e:
        print(f"Exception for DOID {doid}: {str(e)}")
        return None


In [1239]:
process_questions(drugmechdb_filtered_df[0:100])

query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D015464']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D010146']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D006973']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D012223']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease

In [1305]:
process_questions(drugmechdb_filtered_df[0:250])

query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D053202']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D043183']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D056587']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D018879']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease

In [37]:
drugmechdb_filtered_df["question"].nunique()

798

In [35]:
drugmechdb_filtered_df[["disease", "Drug_MeshID"]].nunique()

disease        295
Drug_MeshID    508
dtype: int64

In [2260]:
def serialize_result(result):
    return zlib.compress(json.dumps(result).encode())

# Function to decompress and deserialize JSON
def deserialize_result(serialized_result):
    return json.loads(zlib.decompress(serialized_result).decode())

# Initialize a DataFrame to store results
try:
    results_df = pd.read_parquet("data/analysis_results/bte_results.parquet")  # Load existing results
except FileNotFoundError:
    results_df = pd.DataFrame(columns=["entity_id", "type", "context"])

# Function to save results to a file
def save_results():
    results_df.to_parquet("data/analysis_results/bte_results.parquet", compression="snappy")

# Main processing function
def process_diseases(drugmechdb_filtered_df):  # **Renamed function to reflect the new purpose**
    global results_df

    # Extract already processed entity IDs
    processed_entity_ids = set(results_df["entity_id"])

    for _, row in drugmechdb_filtered_df.iterrows():
        disease_id = row["disease"]  # Take disease ID directly from the column

        # Skip entities that are None or already processed
        if disease_id is None or disease_id in processed_entity_ids:
            continue

        # Retrieve context using BTE
        try:
            context = get_node_context(disease_id, is_disease=True)  # **Pass disease ID directly**
            if context is None:
                raise ValueError("BTE returned no context.")
            serialized_context = serialize_result(context)
        except Exception as e:
            serialized_context = f"error: {str(e)}"

        # Append result to DataFrame
        new_row = pd.DataFrame({
            "entity_id": [disease_id],
            "type": ["disease"],  # **Hardcoded entity type as 'disease'**
            "context": [serialized_context]
        })
        results_df = pd.concat([results_df, new_row], ignore_index=True)

        # Update processed entity IDs and save results
        processed_entity_ids.add(disease_id)
        save_results()

In [2400]:
def serialize_result(result):
    return zlib.compress(json.dumps(result).encode())

# Function to decompress and deserialize JSON
def deserialize_result(serialized_result):
    return json.loads(zlib.decompress(serialized_result).decode())

# Initialize a DataFrame to store results
try:
    results_df = pd.read_parquet("data/analysis_results/bte_results.parquet")  # Load existing results
except FileNotFoundError:
    results_df = pd.DataFrame(columns=["entity_id", "type", "context"])

# Function to save results to a file
def save_results():
    results_df.to_parquet("data/analysis_results/bte_results.parquet", compression="snappy")

# Main processing function
def process_diseases(drugmechdb_filtered_df):  # **Renamed function to reflect the new purpose**
    global results_df

    # Extract already processed entity IDs
    processed_entity_ids = set(results_df["entity_id"])

    for _, row in drugmechdb_filtered_df.iterrows():
        # disease_id = row["disease"]  # Take disease ID directly from the column
        drug_id = row["Drug_MeshID"]

        # Skip entities that are None or already processed
        # if disease_id is None or disease_id in processed_entity_ids:
        #     continue

        if drug_id is None or drug_id in processed_entity_ids:
            continue

        # Retrieve context using BTE
        try:
            context = get_node_context(drug_id, is_disease=False)  # **Pass disease ID directly**
            if context is None:
                raise ValueError("BTE returned no context.")
            serialized_context = serialize_result(context)
        except Exception as e:
            serialized_context = f"error: {str(e)}"

        # Append result to DataFrame
        new_row = pd.DataFrame({
            "entity_id": [drug_id],
            "type": ["drug"],  # **Hardcoded entity type as 'disease'**
            "context": [serialized_context]
        })
        results_df = pd.concat([results_df, new_row], ignore_index=True)

        # Update processed entity IDs and save results
        processed_entity_ids.add(drug_id)
        save_results()

In [2268]:
process_diseases(drugmechdb_filtered_df)

query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D005871']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D006962']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D007383']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D013921']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease

In [2350]:
process_diseases(drugmechdb_filtered_df)

query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:ChemicalEntity'], 'ids': ['DRUGBANK:DB00007']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:ChemicalEntity'], 'ids': ['DRUGBANK:DB01340']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:ChemicalEntity'], 'ids': ['DRUGBANK:DB01246']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:ChemicalEntity'], 'ids': ['DRUGBANK:DB11824']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
query: {'message': {'query_graph': {'nod

In [2401]:
process_diseases(drugmechdb_filtered_df)

query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:ChemicalEntity'], 'ids': ['MESH:D043343']}, 'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}


In [2399]:
# # save bte_results.parquet to bte_results.csv
# bte_parquet.to_parquet("data/analysis_results/bte_results.parquet", index=False)

In [39]:
bte_parquet = pd.read_parquet("data/analysis_results/bte_results.parquet")
bte_parquet.shape

(937, 4)

In [40]:
bte_parquet["type"].value_counts()

type
drug       571
disease    366
Name: count, dtype: int64

In [41]:
# Decode the 'context' column safely from bytes to strings
bte_parquet["context_decoded"] = bte_parquet["context"].apply(
    lambda x: x.decode("utf-8", errors="replace") if isinstance(x, bytes) else x
)

# Filter rows where 'context_decoded' contains the word 'error'
error_rows = bte_parquet[bte_parquet["context_decoded"].str.contains("error", na=False)]

# Display the filtered rows
# print(error_rows)

# Check the shape of the filtered DataFrame
print(error_rows.shape)



(0, 4)


In [42]:
# use deserialize_result to get the context for 'MESH:D001714' in column entity_id from bte_parquet
row_index = bte_parquet[bte_parquet["entity_id"] == "MESH:D043343"].index[0]

# Deserialize the context for the found row
context = deserialize_result(bte_parquet.loc[row_index, "context"])

In [43]:
context

{'description': 'Query processed successfully, retrieved 7569 results.',
 'schema_version': '1.5.0',
 'biolink_version': '4.2.2',
 'workflow': [{'id': 'lookup_and_score'}],
 'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:ChemicalEntity'],
     'ids': ['MESH:D043343']},
    'n1': {'categories': ['biolink:Gene', 'biolink:Protein']}},
   'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}},
  'knowledge_graph': {'nodes': {'CHEBI:9463': {'categories': ['biolink:SmallMolecule'],
     'name': 'Testosterone cypionate',
     'attributes': [{'attribute_type_id': 'biolink:xref',
       'value': ['CHEBI:9463',
        'UNII:M0XW1UBI14',
        'PUBCHEM.COMPOUND:441404',
        'CHEMBL.COMPOUND:CHEMBL1201101',
        'DRUGBANK:DB13943',
        'MESH:C016131',
        'CAS:58-20-8',
        'DrugCentral:4454',
        'KEGG.COMPOUND:C08156',
        'INCHIKEY:HPFVBGJFAYZEBE-ZLQWOROUSA-N',
        'UMLS:C0076181',
        'RXCUI:835827',
        'CHEBI:9464',
        'UNII:

## Metabolite 

In [58]:
DMDB_chebi_metabolite = pd.read_csv("DMDB_benchmark/Benchmarks/DMDB_chebi_metabolite_filtered.csv")
DMDB_chebi_metabolite.shape

(201, 19)

In [59]:
# DMDB_multiple_genes_disease_drug = DMDB_multiple_genes[["disease", "disease_name", "drug","drug_name"]]
DMDB_chebi_metabolite_disease_drug = DMDB_chebi_metabolite[["disease", "disease_name", "Drug_MeshID","drug_name"]]
DMDB_chebi_metabolite_disease_drug.shape

(201, 4)

In [60]:
# pivot DMDB_multiple_genes_disease_drug so that we have 3 columns "entity_id", "type" which contains either "disease" or "drug" and "name" which contains disease_name or drug_name
DMDB_chebi_metabolite_disease_drug_pivot = pd.melt(DMDB_chebi_metabolite_disease_drug, value_vars=["disease", "Drug_MeshID"], var_name="type", value_name="entity_id")
DMDB_chebi_metabolite_disease_drug_pivot["name"] = pd.melt(DMDB_chebi_metabolite_disease_drug, value_vars=["disease_name", "drug_name"], value_name="name")["name"]
DMDB_chebi_metabolite_disease_drug_pivot["type"] = DMDB_chebi_metabolite_disease_drug_pivot["type"].map({"disease": "disease", "Drug_MeshID": "drug"})

In [61]:
DMDB_chebi_metabolite_disease_drug_pivot[DMDB_chebi_metabolite_disease_drug_pivot[["entity_id", "name"]].duplicated(keep=False)].head(10)


type     entity_id                       name
0   disease  MESH:D007634                  Keratitis
2   disease  MESH:D011656        Pulmonary emphysema
3   disease  MESH:D003924  Diabetes Mellitus, Type 2
5   disease  MESH:D003924  Diabetes Mellitus, Type 2
7   disease  MESH:D007634                  Keratitis
11  disease  MESH:D006501     Hepatic Encephalopathy
12  disease  MESH:D006973               Hypertension
18  disease  MESH:D012559              Schizophrenia
19  disease  MESH:D001249                     Asthma
20  disease  MESH:D003555                 Cystinuria

In [62]:
# drop duplicates from DMDB_multiple_genes_disease_drug_pivot
DMDB_chebi_metabolite_disease_drug_pivot = DMDB_chebi_metabolite_disease_drug_pivot.drop_duplicates()
DMDB_chebi_metabolite_disease_drug_pivot.shape

(253, 3)

In [63]:
# find nunique of "entity_id" and "name" in DMDB_multiple_genes_disease_drug_pivot
DMDB_chebi_metabolite_disease_drug_pivot[["entity_id", "name"]].nunique()

entity_id    253
name         253
dtype: int64

In [80]:
# removed "disease" from categories
import pandas as pd
import json
import zlib

def get_node_context(entity_id, entity_type):

    try:
        # Map the entity type to the corresponding Biolink category
        category = "biolink:Disease" if entity_type.lower() == "disease" else "biolink:ChemicalEntity"
        
        base_uri = "https://bte.transltr.io/v1/query"
        query = {
            "message": {
                "query_graph": {
                    "nodes": {
                        "n0": {"categories": [category], "ids": [entity_id]},
                        "n1": {"categories": ["biolink:ChemicalEntity"]}
                    },
                    "edges": {
                        "e01": {"subject": "n0", "object": "n1"}
                    }
                }
            }
        }
        
        print("Sending query:", query)
        result = get_bte_api_resp(base_uri, query)
        
        if result.get('status') == 500:
            print(f"Error from BTE API for {entity_id}: {result.get('description', 'No description provided')}")
            return None
        
        return result

    except Exception as e:
        print(f"Exception for {entity_id}: {e}")
        return None




In [81]:
def serialize_result(result):
    """Compress and serialize a JSON-compatible object."""
    return zlib.compress(json.dumps(result).encode())

def deserialize_result(serialized_result):
    """Decompress and deserialize the stored context."""
    return json.loads(zlib.decompress(serialized_result).decode())

# def process_entities(df, results_filepath="data/analysis_results/DMDB_multiple_genes_bte_results.parquet"):
def process_entities(df, results_filepath="data/analysis_results/DMDB_chebi_metabolite_bte_results_V2.parquet"):
    """
    Process entities from the input DataFrame to retrieve their BTE context.
    
    Parameters:
      - df: A DataFrame with at least the columns 'type' and 'entity_id'.
      - results_filepath: Path to the file where results are stored.
      
    Returns:
      - A DataFrame with the retrieved context for each entity.
    """
    try:
        results_df = pd.read_parquet(results_filepath)
    except FileNotFoundError:
        results_df = pd.DataFrame(columns=["entity_id", "name", "type", "context"])

    # Keep track of already processed entity IDs to avoid duplicates
    processed_entity_ids = set(results_df["entity_id"])

    for _, row in df.iterrows():
        entity_id = row["entity_id"]
        entity_type = row["type"]
        name = row["name"]

        if entity_id is None or entity_id in processed_entity_ids:
            continue

        context = get_node_context(entity_id, entity_type)
        if context is None:
            serialized_context = None  # You might log or handle errors here as needed
        else:
            serialized_context = serialize_result(context)

        new_row = pd.DataFrame({
            "entity_id": [entity_id],
            "name": [name],
            "type": [entity_type],
            "context": [serialized_context]
        })
        results_df = pd.concat([results_df, new_row], ignore_index=True)
        processed_entity_ids.add(entity_id)

        # Save after each new entry (adjust frequency as desired)
        results_df.to_parquet(results_filepath, compression="snappy")
    
    # return results_df



In [57]:
# Example usage on your DataFrame subset:
# df_subset = DMDB_multiple_genes_disease_drug_pivot.head(3)
process_entities(DMDB_chebi_metabolite_disease_drug_pivot)

Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D007634']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D009855']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D014806']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D001361']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Dis

In [73]:
process_entities(DMDB_chebi_metabolite_disease_drug_pivot)

Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D003924']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D013274']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D010661']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:ChemicalEntity'], 'ids': ['MESH:C502994']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biol

In [82]:
process_entities(DMDB_chebi_metabolite_disease_drug_pivot)

Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D014552']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D010032']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D014605']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Disease'], 'ids': ['MESH:D006501']}, 'n1': {'categories': ['biolink:ChemicalEntity']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:Dis

In [57]:
DMDB_chebi_metabolite_bte_parquet = pd.read_parquet("data/analysis_results/DMDB_chebi_metabolite_bte_results_V2.parquet")
DMDB_chebi_metabolite_bte_parquet.shape

(381, 4)

In [65]:
# context = deserialize_result(DMDB_chebi_metabolite_bte_parquet.loc[1, "context"])
# context

In [61]:
# DMDB_chebi_metabolite_bte_parquet.to_parquet("data/analysis_results/DMDB_chebi_metabolite_bte_results_V2.parquet")

## Biological Process

In [68]:
DMDB_go_bp_df = pd.read_csv("DMDB_benchmark/Benchmarks/DMDB_go_bp_filtered.csv")
DMDB_go_bp_df.shape

(842, 16)

In [69]:
DMDB_bp_sampled_disease_go = DMDB_go_bp_df[["disease", "disease_name", "bp","bp_name"]]
DMDB_bp_sampled_disease_go.shape

(842, 4)

In [70]:
DMDB_bp_sampled_disease_go_pivot = pd.melt(DMDB_bp_sampled_disease_go, value_vars=["disease", "bp"], var_name="type", value_name="entity_id")
DMDB_bp_sampled_disease_go_pivot["name"] = pd.melt(DMDB_bp_sampled_disease_go, value_vars=["disease_name", "bp_name"], value_name="name")["name"]
DMDB_bp_sampled_disease_go_pivot["type"] = DMDB_bp_sampled_disease_go_pivot["type"].map({"disease": "disease", "bp": "go"})
DMDB_bp_sampled_disease_go_pivot.shape

(1684, 3)

In [71]:
DMDB_bp_sampled_disease_go_pivot = DMDB_bp_sampled_disease_go_pivot.drop_duplicates()
DMDB_bp_sampled_disease_go_pivot.shape

(605, 3)

In [72]:
DMDB_bp_sampled_disease_go_pivot[["entity_id", "name"]].nunique()

entity_id    605
name         602
dtype: int64

In [73]:
DMDB_bp_sampled_disease_go_pivot["type"].value_counts()

type
disease    378
go         227
Name: count, dtype: int64

In [74]:
def get_node_context(entity_id, entity_type):
    try:
        # Determine category for n0 and n1 based on entity_type
        if entity_type.lower() == "disease":
            category_n0 = "biolink:Disease"
            category_n1 = ["biolink:ChemicalEntity"]
        else:  # biological process or activity
            category_n0 = "biolink:BiologicalProcessOrActivity"
            category_n1 = ["biolink:Gene"]

        base_uri = "https://bte.transltr.io/v1/query"
        query = {
            "message": {
                "query_graph": {
                    "nodes": {
                        "n0": {"categories": [category_n0], "ids": [entity_id]},
                        "n1": {"categories": category_n1}
                    },
                    "edges": {
                        "e01": {"subject": "n0", "object": "n1"}
                    }
                }
            }
        }

        print("Sending query:", query)
        result = get_bte_api_resp(base_uri, query)

        if result.get('status') == 500:
            print(f"Error from BTE API for {entity_id}: {result.get('description', 'No description provided')}")
            return None

        return result

    except Exception as e:
        print(f"Exception for {entity_id}: {e}")
        return None

In [75]:
def serialize_result(result):
    """Compress and serialize a JSON-compatible object."""
    return zlib.compress(json.dumps(result).encode())

def deserialize_result(serialized_result):
    """Decompress and deserialize the stored context."""
    return json.loads(zlib.decompress(serialized_result).decode())

# def process_entities(df, results_filepath="data/analysis_results/DMDB_go_bp_sampled.parquet"):  #first run, category_n0 = "biolink:Disease", category_n1 = ["biolink:ChemicalEntity", "biolink:BiologicalProcessOrActivity"]
# def process_entities(df, results_filepath="data/analysis_results/DMDB_go_bp_sampled_separately.parquet"): #second run; category_n0 = "biolink:Disease", category_n1 = ["biolink:ChemicalEntity"] and separately ,category_n0 = "biolink:Disease", category_n1 ="biolink:BiologicalProcessOrActivity"]
def process_entities(df, results_filepath="data/analysis_results/DMDB_go_bp_sampled_separately_V2.parquet"): #third run; category_n0 = "biolink:BiologicalProcessOrActivity", category_n1 = ["biolink:Gene"] and separately ,category_n0 = "biolink:Disease", category_n1 ="ChemicalEntity"
    """
    Process entities from the input DataFrame to retrieve their BTE context.
    
    Parameters:
      - df: A DataFrame with at least the columns 'type' and 'entity_id'.
      - results_filepath: Path to the file where results are stored.
      
    Returns:
      - A DataFrame with the retrieved context for each entity.
    """
    try:
        results_df = pd.read_parquet(results_filepath)
    except FileNotFoundError:
        results_df = pd.DataFrame(columns=["entity_id", "name", "type", "context"])

    # Keep track of already processed entity IDs to avoid duplicates
    processed_entity_ids = set(results_df["entity_id"])

    for _, row in df.iterrows():
        entity_id = row["entity_id"]
        entity_type = row["type"]
        name = row["name"]

        if entity_id is None or entity_id in processed_entity_ids:
            continue

        context = get_node_context(entity_id, entity_type)
        if context is None:
            serialized_context = None  # You might log or handle errors here as needed
        else:
            serialized_context = serialize_result(context)

        new_row = pd.DataFrame({
            "entity_id": [entity_id],
            "name": [name],
            "type": [entity_type],
            "context": [serialized_context]
        })
        results_df = pd.concat([results_df, new_row], ignore_index=True)
        processed_entity_ids.add(entity_id)

        # Save after each new entry (adjust frequency as desired)
        results_df.to_parquet(results_filepath, compression="snappy")
    
    # return results_df

In [1469]:
# Example usage on your DataFrame subset:
# df_subset = DMDB_multiple_genes_disease_drug_pivot.head(3)
process_entities(DMDB_bp_sampled_disease_go_pivot)

Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:BiologicalProcessOrActivity'], 'ids': ['GO:0006696']}, 'n1': {'categories': ['biolink:Gene']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:BiologicalProcessOrActivity'], 'ids': ['GO:0042311']}, 'n1': {'categories': ['biolink:Gene']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:BiologicalProcessOrActivity'], 'ids': ['GO:0016298']}, 'n1': {'categories': ['biolink:Gene']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n0': {'categories': ['biolink:BiologicalProcessOrActivity'], 'ids': ['GO:0008800']}, 'n1': {'categories': ['biolink:Gene']}}, 'edges': {'e01': {'subject': 'n0', 'object': 'n1'}}}}}
Sending query: {'message': {'query_graph': {'nodes': {'n

In [76]:
DMDB_go_bp_sep_bte_parquet = pd.read_parquet("data/analysis_results/DMDB_go_bp_sampled_separately_V2.parquet")
DMDB_go_bp_sep_bte_parquet.shape

(605, 5)

In [77]:
DMDB_bp_sampled_disease_go_pivot["type"].value_counts()

type
disease    378
go         227
Name: count, dtype: int64

In [78]:
# context = deserialize_result(DMDB_go_bp_sep_bte_parquet.loc[21, "context"])
# context

In [79]:
def extract_results_count_with_deserialization(context_str):
    try:
        context_dict = deserialize_result(context_str)
        description = context_dict.get("description", "")
        match = re.search(r"retrieved (\d+) results", description)
        return int(match.group(1)) if match else None
    except Exception:
        return None

# Apply to all rows
DMDB_go_bp_sep_bte_parquet["results"] = DMDB_go_bp_sep_bte_parquet["context"].apply(extract_results_count_with_deserialization)

In [80]:
DMDB_go_bp_sep_bte_parquet[["entity_id", "name","type","results"]].head(2)

entity_id                         name     type  results
0  MESH:D004927  Escherichia coli Infections  disease      170
1  MESH:D011618          Psychotic Disorders  disease      925

In [81]:
none_count = 0
error_count = 0
valid_count = 0

for index, row in DMDB_go_bp_sep_bte_parquet.iterrows():
    context = row["context"]
    if context is None:
        none_count += 1
    elif isinstance(context, str) and context.startswith("error:"):
        error_count += 1
    else:
        valid_count += 1

print("Rows with context = None:", none_count)
print("Rows with error context:", error_count)
print("Rows with valid context:", valid_count)

Rows with context = None: 0
Rows with error context: 0
Rows with valid context: 605
